In [18]:
#импорт библиотек
import pandas as pd
import numpy as np
import nltk
from sklearn.ensemble import RandomForestClassifier
from sklearn.multioutput import MultiOutputClassifier
import re 
from nltk.stem import WordNetLemmatizer 
from pymystem3 import Mystem
from tqdm import tqdm
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer     
from sklearn.metrics import recall_score
from sklearn.model_selection import train_test_split


In [2]:
#загрузка данных
df_train = pd.read_csv("D:\\DS\\Выявление элементов культурного кода россиян в отзывах о произведениях художественной литературы\\train_dataset_train.csv")
df_test = pd.read_csv("D:\\DS\\Выявление элементов культурного кода россиян в отзывах о произведениях художественной литературы\\test_dataset_test.csv")

#посмтрим на типы данных и нет ли пропусков
print(df_train.info())
print(df_test.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4839 entries, 0 to 4838
Data columns (total 17 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   RecordNo                              4839 non-null   int64  
 1   Название книги                        4839 non-null   object 
 2   Автор                                 4839 non-null   object 
 3   Ссылка на литрес                      4839 non-null   object 
 4   Рейтинг                               4839 non-null   float64
 5   Количество оценок                     4839 non-null   int64  
 6   Количество отзывов                    4839 non-null   int64  
 7   Имя читателя                          4839 non-null   object 
 8   Оценка книги читателем (из 5 баллов)  4070 non-null   float64
 9   Отзыв                                 4839 non-null   object 
 10  Лайки на отзыв                        4839 non-null   int64  
 11  Дислайки на отзыв

In [3]:
#посмотрим сами данные для обучения
df_train.head(14)

RecordNo                       Название книги               Автор  \
0       6145              Зулейха открывает глаза        Гузель Яхина   
1       7006              Зулейха открывает глаза        Гузель Яхина   
2       1124                             Дети мои        Гузель Яхина   
3       4716                                 ПОСТ  Дмитрий Глуховский   
4       2946                                 ПОСТ  Дмитрий Глуховский   
5        592                               Санькя      Захар Прилепин   
6       7635                              Обитель      Захар Прилепин   
7       7226                          Батюшки мои   Валентин Курбатов   
8       6194              Зулейха открывает глаза        Гузель Яхина   
9       3276                                Текст  Дмитрий Глуховский   
10      5321                       Женщины Лазаря     Марина Степнова   
11      3383                            Ампир «В»      Виктор Пелевин   
12        80  Прощание с Матерой. Пожар (сборник)   Валентин Распутин   
13      4990              Зулейха открывает глаза        Гузель Яхина   

                                     Ссылка на литрес  Рейтинг  \
0   https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.7   
1   https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.6   
2        https://www.litres.ru/guzel-yahina/deti-moi/      4.4   
3      https://www.litres.ru/dmitriy-gluhovskiy/post/      3.9   
4   https://www.litres.ru/dmitriy-gluhovskiy/post-...      4.4   
5   https://www.litres.ru/zahar-prilepin/sankya-16...      4.1   
6        https://www.litres.ru/zahar-prilepin/obitel/      4.5   
7   https://www.litres.ru/valentin-kurbatov/batush...      4.7   
8   https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.7   
9     https://www.litres.ru/dmitriy-gluhovskiy/tekst/      4.4   
10  https://www.litres.ru/marina-stepnova/zhenschi...      4.7   
11      https://www.litres.ru/viktor-pelevin/ampir-v/      4.5   
12  https://www.litres.ru/valentin-rasputin/prosch...      4.2   
13  https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.6   

    Количество оценок  Количество отзывов     Имя читателя  \
0                3922                 408    Айгуль Ляпина   
1               24719                2103           Olga T   
2                8032                 702   Кирилл Чириков   
3                 430                  48     Kimetov Oleg   
4                 832                 113   Сергей Никитин   
5                 274                  37         Кирилл К   
6                1916                 171   Сергей Киряков   
7                   3                   6  Елена Тимофеева   
8                3922                 408        yuliya_bv   
9                7276                 622     shilina.anna   
10               1689                 137   Anna Subbotina   
11                572                  47  Ольга Воробьева   
12                 46                   5       ele-efimov   
13              24719                2103  Cветлана Бобырь   

    Оценка книги читателем (из 5 баллов)  \
0                                    5.0   
1                                    5.0   
2                                    5.0   
3                                    5.0   
4                                    5.0   
5                                    3.0   
6                                    5.0   
7                                    NaN   
8                                    5.0   
9                                    5.0   
10                                   5.0   
11                                   NaN   
12                                   NaN   
13                                   4.0   

                                                Отзыв  Лайки на отзыв  \
0   Рекомендую книгу в прочтению/прослушиванию. Ес...               0   
1   Удивительно, что сейчас возникает ТАКАЯ литера...               0   
2   Душевно, жизненно, чувственно, проникновенно!!...               0   
3   Очень понравилось. Причем пон

In [4]:
#проанализируем данные на выбросы
df_train.describe()

RecordNo      Рейтинг  Количество оценок  Количество отзывов  \
count  4839.000000  4839.000000        4839.000000         4839.000000   
mean   4022.292829     4.504546        8864.133499          764.269890   
std    2297.657785     0.189645        9956.818440          841.728494   
min       2.000000     3.200000           1.000000            1.000000   
25%    2042.000000     4.400000        1212.000000          113.000000   
50%    4058.000000     4.600000        3551.000000          285.000000   
75%    6028.000000     4.600000       24719.000000         2103.000000   
max    7960.000000     5.000000       24719.000000         2103.000000   

       Оценка книги читателем (из 5 баллов)  Лайки на отзыв  \
count                           4070.000000     4839.000000   
mean                               4.502703        4.025832   
std                                1.035078       26.075881   
min                                1.000000        0.000000   
25%                                5.000000        0.000000   
50%                                5.000000        0.000000   
75%                                5.000000        2.000000   
max                                5.000000      874.000000   

       Дислайки на отзыв  Релевантность  Таксономия релевантные  \
count        4839.000000    4839.000000             4839.000000   
mean            1.790453       0.218640                0.512296   
std            10.973393       0.413367                0.499900   
min             0.000000       0.000000                0.000000   
25%             0.000000       0.000000                0.000000   
50%             1.000000       0.000000                1.000000   
75%             1.000000       0.000000                1.000000   
max           459.000000       1.000000                1.000000   

       Таксономия не релевантные  Длина отзыва     Ценности  
count                4839.000000   4839.000000  4839.000000  
mean                    0.126886      0.234759     0.542054  
std                     0.332879      0.423892     0.498280  
min                     0.000000      0.000000     0.000000  
25%                     0.000000      0.000000     0.000000  
50%                     0.000000      0.000000     1.000000  
75%                     0.000000      0.000000     1.000000  
max                     1.000000      1.000000     1.000000

In [5]:
#не будем анализировать отзывы, которые получили свыше 30 дизлайков
df_train = df_train[df_train["Дислайки на отзыв"] <= 30]

In [6]:
#Напишем функцию для удаления строк за пределами квантилей (с небольшим запасом): меньше q25*0.25 и больше q75*2   
def delete_data(data,column):
    q25=np.array(data[column].quantile(0.25))
    q75=np.array(data[column].quantile(0.75))  
    first_part=q25*0.25
    second_part=q75*2
    delete_index = []
    for index_value, value in zip(data[column].index,data[column]):
        if second_part <= value or value <= first_part:
            delete_index.append(index_value)
    print('Количество строк, выбранных для удаления ' + str(column)+":",len(delete_index))
    return delete_index

In [7]:
column = ["Количество оценок","Количество отзывов"]
count = 0 
#удалим выбросы, то есть данные, которые меньше q25*0.25 и больше q75*2
for i in column:
    delete_index = delete_data(df_train,i)
    count += len(delete_index)
    df_train = df_train.drop(delete_index,axis = 0)
print("Было удалено:", count)
df_train = df_train.reset_index(drop=True)
df_train.describe()

Количество строк, выбранных для удаления Количество оценок: 614
Количество строк, выбранных для удаления Количество отзывов: 65
Было удалено: 679


RecordNo      Рейтинг  Количество оценок  Количество отзывов  \
count  4135.000000  4135.000000        4135.000000         4135.000000   
mean   4047.461911     4.525611       10240.878356          882.169770   
std    2287.836921     0.135211       10032.596241          846.593331   
min       2.000000     3.900000         340.000000           47.000000   
25%    2071.000000     4.400000        1916.000000          171.000000   
50%    4111.000000     4.600000        7276.000000          622.000000   
75%    6038.000000     4.600000       24719.000000         2103.000000   
max    7960.000000     4.800000       24719.000000         2103.000000   

       Оценка книги читателем (из 5 баллов)  Лайки на отзыв  \
count                           3599.000000     4135.000000   
mean                               4.529869        2.701330   
std                                1.016339        9.872336   
min                                1.000000        0.000000   
25%                                5.000000        0.000000   
50%                                5.000000        0.000000   
75%                                5.000000        2.000000   
max                                5.000000      178.000000   

       Дислайки на отзыв  Релевантность  Таксономия релевантные  \
count        4135.000000    4135.000000             4135.000000   
mean            1.331318       0.214027                0.513906   
std             2.519306       0.410195                0.499867   
min             0.000000       0.000000                0.000000   
25%             0.000000       0.000000                0.000000   
50%             1.000000       0.000000                1.000000   
75%             1.000000       0.000000                1.000000   
max            29.000000       1.000000                1.000000   

       Таксономия не релевантные  Длина отзыва     Ценности  
count                4135.000000   4135.000000  4135.000000  
mean                    0.132527      0.243289     0.526239  
std                     0.339104      0.429120     0.499371  
min                     0.000000      0.000000     0.000000  
25%                     0.000000      0.000000     0.000000  
50%                     0.000000      0.000000     1.000000  
75%                     0.000000      0.000000     1.000000  
max                     1.000000      1.000000     1.000000

In [8]:
#объединим все отзывы в одну строку с разделителем '/br', чтобы лемматизация отработала быстрее
alltexts_train = ''
for i in tqdm(range(len(df_train['Отзыв']))):
    alltexts_train = ''.join([alltexts_train + ' br ' + df_train.loc[i, 'Отзыв']])
print(alltexts_train)

100%|████████████████████████████████████████████████████████████████████████████| 4135/4135 [00:01<00:00, 2265.52it/s]

 br Рекомендую книгу в прочтению/прослушиванию. Есть о чем задуматься… Написано тоже осень хорошо. Иногда даже всплакнуть хотелось. Рада, что не жила в то время. br Удивительно, что сейчас возникает ТАКАЯ литература. Заставляет задуматься о кулаках (в школе ведь нам рассказывали совсем другое), о жизни татарских женщин и взглядах на мир. Книга понравилась. Местами с написано немного наивно и простовато. Тем не менее, прочитать однозначно стоит. br Душевно, жизненно, чувственно, проникновенно!!!! История, которая проникает в мысли, непринуждённости заставляет задуматься о смысле бытия, об отношениях между близкими и семье!!! В очередной раз убедилась о силе слов, каждое сказанное, написанное слово- новый мир, вселенная!!! br Очень понравилось. Причем понравилось больше «Метро». «Метро» распиаренная история (что автор и не скрывает). А тут и герои раскрыты, и мотивы их понятны, и их выбор. Присутствует конфликт отцов и детей. Любовная линия. По стилю очень походит на первые романы Лукьян

In [9]:
#лемматизация
lmtzr = Mystem()
pattern_train = re.sub(r'[^а-яА-ЯёЁ ]', 'br', alltexts_train)
clear_train = pattern_train.split()
corpus_train = " ".join(lmtzr.lemmatize(alltexts_train))
print(corpus_train)


  br   рекомендовать   книга   в   прочтение / прослушивание .  быть   о   что   задумываться …  написать   тоже   осень   хорошо .  иногда   даже   всплакнуть   хотеться .  рад ,  что   не   жить   в   тот   время .   br   удивительно ,  что   сейчас   возникать   такой   литература .  заставлять   задумываться   о   кулак  ( в   школа   ведь   мы   рассказывать   совсем   другой ),  о   жизнь   татарский   женщина   и   взгляд   на   мир .  книга   понравиться .  место   с   написать   немного   наивный   и   простоватый .  то   не   менее ,  прочитывать   однозначно   стоять .   br   душевно ,  жизненно ,  чувственно ,  проникновенный !!!!  история ,  который   проникать   в   мысль ,  непринужденность   заставлять   задумываться   о   смысл   бытие ,  об   отношение   между   близкий   и   семья !!!  в   очередной   раз   убеждаться   о   сила   слово ,  каждый   сказать ,  написать   слово -  новый   мир ,  вселенная !!!   br   очень   понравиться .  причем   понравиться   много  

In [10]:
#вернем отзывы в data frame
lemm_df_train = pd.DataFrame(corpus_train.split(' br '))
lemm_df_train = lemm_df_train.drop(df_train.index[[0,0]])
lemm_df_train = lemm_df_train.reset_index(drop=True)
lemm_df_train[0]

0         рекомендовать   книга   в   прочтение / прос...
1         удивительно ,  что   сейчас   возникать   та...
2         душевно ,  жизненно ,  чувственно ,  проникн...
3         очень   понравиться .  причем   понравиться ...
4         круто .  автор   и   он   же   чтец  –  гени...
                              ...                        
4130      еще   один   замечательный   роман   гузель ...
4131      как   всегда   у   водолазкин  –  увлекатель...
4132      мрачно ,  грустно .  давно   такой   не   чи...
4133      очень   интересный   книга !  как   будто   ...
4134      тот   редкий   случай ,  когда ,  ничто   ос...
Name: 0, Length: 4135, dtype: object

In [11]:
df_train['Отзыв после лемматизации'] = lemm_df_train[0]
df_train

RecordNo           Название книги               Автор  \
0         6145  Зулейха открывает глаза        Гузель Яхина   
1         7006  Зулейха открывает глаза        Гузель Яхина   
2         1124                 Дети мои        Гузель Яхина   
3         4716                     ПОСТ  Дмитрий Глуховский   
4         2946                     ПОСТ  Дмитрий Глуховский   
...        ...                      ...                 ...   
4130      1196                 Дети мои        Гузель Яхина   
4131      1810                  Авиатор  Евгений Водолазкин   
4132      3220                    Текст  Дмитрий Глуховский   
4133      4480  Зулейха открывает глаза        Гузель Яхина   
4134      6849              Дни Савелия  Григорий Служитель   

                                       Ссылка на литрес  Рейтинг  \
0     https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.7   
1     https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.6   
2          https://www.litres.ru/guzel-yahina/deti-moi/      4.4   
3        https://www.litres.ru/dmitriy-gluhovskiy/post/      3.9   
4     https://www.litres.ru/dmitriy-gluhovskiy/post-...      4.4   
...                                                 ...      ...   
4130       https://www.litres.ru/guzel-yahina/deti-moi/      4.4   
4131  https://www.litres.ru/evgeniy-vodolazkin/aviator/      4.5   
4132  https://www.litres.ru/dmitriy-gluhovskiy/tekst...      4.5   
4133  https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.6   
4134  https://www.litres.ru/grigoriy-sluzhitel/dni-s...      4.6   

      Количество оценок  Количество отзывов        Имя читателя  \
0                  3922                 408       Айгуль Ляпина   
1                 24719                2103              Olga T   
2                  8032                 702      Кирилл Чириков   
3                   430                  48        Kimetov Oleg   
4                   832                 113      Сергей Никитин   
...                 ...                 ...                 ...   
4130               8032                 702           417504557   
4131               3551                 260  Viktoria Steinbach   
4132               1923                 246               AnVer   
4133              24719                2103     Мария Перешивко   
4134               1212                 143  Christine Komtsian   

      Оценка книги читателем (из 5 баллов)  \
0                                      5.0   
1                                      5.0   
2                                      5.0   
3                                      5.0   
4                                      5.0   
...                                    ...   
4130                                   4.0   
4131                                   NaN   
4132                                   5.0   
4133                                   5.0   
4134                                   5.0   

                                                  Отзыв  Лайки на отзыв  \
0     Рекомендую книгу в прочтению/прослушиванию. Ес...               0   
1     Удивительно, что сейчас возникает ТАКАЯ литера...               0   
2     Душевно, жизненно, чувственно, проникновенно!!...               0   
3     Очень понравилось. Причем понравилось больше «...               2   
4     Круто. Автор и он же чтец – гений. Прослушал н...               1   
...                                                 ...             ...   
4130  Ещё один замечательный роман Гузель Яхиной! По...               0   
4131  Как всегда у Водолазкина – увлекательнейший сю...               0   
4132  Мрачно, грустно. Давно такого не читала и хват...               1   
4133  Очень интересная книга! Как будто очутилась в ...               0   
4134  Тот редкий случай, когда, ничего особенно не о...               0   

      Дислайки на отзыв  Релевантность  Таксономия релевантные  \
0                     3              0                       0   
1                     1              0   

In [12]:
#проведем лемматтизацию тестовых данных
#объединим все отзывы в одну строку с разделителем '/br', чтобы лемматизация отработала быстрее
alltexts_test = ''
for i in tqdm(range(len(df_test['Отзыв']))):
    alltexts_test = ''.join([alltexts_test + ' br ' + df_test.loc[i, 'Отзыв']])
print(alltexts_test)

#лемматизация
lmtzr = Mystem()
pattern_test = re.sub(r'[^а-яА-ЯёЁ ]', 'br', alltexts_test)
clear_test = pattern_test.split()
corpus_test = " ".join(lmtzr.lemmatize(alltexts_test))
print(corpus_test)

lemm_df_test = pd.DataFrame(corpus_test.split(' br '))
lemm_df_test = lemm_df_test.drop(df_test.index[[0,0]])
lemm_df_test = lemm_df_test.reset_index(drop=True)


df_test['Отзыв после лемматизации'] = lemm_df_test[0]
df_test

100%|████████████████████████████████████████████████████████████████████████████| 2075/2075 [00:00<00:00, 4631.40it/s]


 br Настоящая глубокая книга, коих сейчас очень немного… Про дизнь, как она была и есть. Про чувства и про то, что переживает человек в течение всей своей жизни, независимо от условий.. br Одна из лучших книг прочитанных за последние годы, сравнить могу лишь с Фандориным от Акунина, и то, тут погружение значительно глубже. Почувствовать себя в шкуре главного героя незабываемо. Текст и начитка великолепны. br Тот случай, когда невозможно пройти мимо, не оставив отзыв. Эта книга вырвала меня на пару дней из жизни. Какое-то невероятное погружение, давно такого не испытывала от литературы, чтобы без продыху, без надежды на хоть какое-то переключение внимания.. Браво, Дмитрий! Это было мощно! По ощущениям, есть что-то общее с моим любимым «Щеглом», та же атмосфера беспробудного отчаяния и тоски.. br Очень не глубокая книга. Дочитала до конца, в плане ознакомления. Интересны моменты , где описана татарская изба( очень похоже описано в учебнике 3 класса, по теме «жилище народов моего края»), 

  br   настоящий   глубокий   книга ,  кой   сейчас   очень   немного …  про   дизнь ,  как   она   быть   и   быть .  про   чувство   и   про   то ,  что   переживать   человек   в   течение   весь   свой   жизнь ,  независимо   от   условие ..   br   один   из   хороший   книга   прочитывать   за   последний   год ,  сравнивать   мочь   лишь   с   фандорин   от   акунин ,  и   то ,  тут   погружение   значительно   глубоко .  почувствовать   себя   в   шкура   главный   герой   незабываемый .  текст   и   начиток   великолепный .   br   тот   случай ,  когда   невозможно   проходить   мимо ,  не   оставлять   отзыв .  этот   книга   вырывать   я   на   пара   день   из   жизнь .  какой-то   невероятный   погружение ,  давно   такой   не   испытывать   от   литература ,  чтобы   без   продых ,  без   надежда   на   хоть   какой-то   переключение   внимание ..  браво ,  дмитрий !  это   быть   мощно !  по   ощущение ,  быть   что-то   общий   с   мой   любимый  « щегол »,  тот   же   а

RecordNo               Название книги               Автор  \
0         3366                     Дети мои        Гузель Яхина   
1         3952                        Текст  Дмитрий Глуховский   
2         6852                        Текст  Дмитрий Глуховский   
3         4586      Зулейха открывает глаза        Гузель Яхина   
4         4677      Зулейха открывает глаза        Гузель Яхина   
...        ...                          ...                 ...   
2070      4661      Зулейха открывает глаза        Гузель Яхина   
2071      1547                     Дети мои        Гузель Яхина   
2072      6071      Зулейха открывает глаза        Гузель Яхина   
2073      3805      С неба упали три яблока      Наринэ Абгарян   
2074       471  Лев Толстой: Бегство из рая     Павел Басинский   

                                       Ссылка на литрес  Рейтинг  \
0          https://www.litres.ru/guzel-yahina/deti-moi/      4.4   
1     https://www.litres.ru/dmitriy-gluhovskiy/tekst...      4.5   
2       https://www.litres.ru/dmitriy-gluhovskiy/tekst/      4.4   
3     https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.6   
4     https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.6   
...                                                 ...      ...   
2070  https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.6   
2071       https://www.litres.ru/guzel-yahina/deti-moi/      4.4   
2072  https://www.litres.ru/guzel-yahina/zuleyha-otk...      4.6   
2073  https://www.litres.ru/narine-abgaryan/s-neba-u...      4.8   
2074  https://www.litres.ru/pavel-basinskiy/lev-tols...      4.4   

      Количество оценок  Количество отзывов        Имя читателя  \
0                  8032                 702     Марина Ефимкина   
1                  1923                 246            alexvarp   
2                  7276                 622  fb_154207611938008   
3                 24719                2103     Мария Курочкина   
4                 24719                2103         sahnovavera   
...                 ...                 ...                 ...   
2070              24719                2103  Екатерина Юзбашьян   
2071               8032                 702           239833928   
2072              24719                2103                I be   
2073               1455                 189        Ольга Акопян   
2074                151                  24           559376271   

      Оценка книги читателем (из 5 баллов)  \
0                                      5.0   
1                                      5.0   
2                                      5.0   
3                                      NaN   
4                                      NaN   
...                                    ...   
2070                                   5.0   
2071                                   4.0   
2072                                   5.0   
2073                                   5.0   
2074                                   5.0   

                                                  Отзыв  Лайки на отзыв  \
0     Настоящая глубокая книга, коих сейчас очень не...               2   
1     Одна из лучших книг прочитанных за последние г...               1   
2     Тот случай, когда невозможно пройти мимо, не о...               0   
3     Очень не глубокая книга. Дочитала до конца, в ...               4   
4     Очень понравилась. Читается легко, о непростых...               0   
...                                                 ...             ...   
2070  Очень понравилась!!!! Написана грамотным, крас...               0   
2071  Зулейха понравилась больше. Книга Дети мои каж...               0   
2072  Прочла на одном дыхании, не смотря на раздираю...               0   
2073  нет слов. потрясающе. эту книгу не описать. но...               0   
2074  Великолепная книга. Подробно описаны взаимоотн...               0   

      Дислайки на отзыв                           Отзыв после лемматизации  
0                     0    настоящий   глубокий 

In [13]:
mass_label = ['Релевантность',
       'Таксономия релевантные', 'Таксономия не релевантные',
       'Длина отзыва', 'Ценности']
features = df_train['Отзыв после лемматизации']
target = df_train[mass_label]
#разделим данные для обучения на обучающую и валидационную выборки
features_train, features_valid, target_train, target_valid = train_test_split(features, target, test_size=0.3, random_state=12345)
features_test = df_test['Отзыв после лемматизации'] 
features_test

0         настоящий   глубокий   книга ,  кой   сейчас...
1         один   из   хороший   книга   прочитывать   ...
2         тот   случай ,  когда   невозможно   проходи...
3         очень   не   глубокий   книга .  дочитывать ...
4         очень   понравиться .  читаться   легко ,  о...
                              ...                        
2070      очень   понравиться !!!!  написать   грамотн...
2071      зулейх   понравиться   больше .  книга   реб...
2072      прочитывать   на   один   дыхание ,  не   см...
2073      нет   слово .   потрясающе .   этот   книга ...
2074      великолепный   книга .  подробно   описывать...
Name: Отзыв после лемматизации, Length: 2075, dtype: object

In [14]:
#векторизация
stop = stopwords.words('russian')
count_tf_idf = TfidfVectorizer(stop_words=stop) 

corpus_train = count_tf_idf.fit_transform(features_train)
corpus_valid = count_tf_idf.transform(features_valid)
corpus_test = count_tf_idf.transform(features_test)          


In [19]:
forest = RandomForestClassifier(random_state=12345) 
model = MultiOutputClassifier(forest, n_jobs=-1)
model.fit(corpus_train,target_train) 
predicted_train = model.predict(corpus_train) 
predicted_valid = model.predict(corpus_valid) 
print("Recall score обучающей выборки:", recall_score(target_train, predicted_train, average='macro'))
print("Recall score валидационной выборки:", recall_score(target_valid, predicted_valid, average='macro'))

Recall score обучающей выборки: 1.0
Recall score валидационной выборки: 0.575993652912288


In [20]:
#получим предсказания для тестовой выборки
predicted_test = model.predict(corpus_test) 
predicted_test

array([[0, 0, 0, 1, 1],
       [0, 1, 0, 0, 0],
       [0, 0, 0, 0, 1],
       ...,
       [1, 1, 0, 0, 1],
       [0, 1, 0, 0, 1],
       [0, 0, 0, 0, 1]], dtype=int64)

In [21]:
#добавим заголовки для предсказаний согласно формату загрузки результатов
res = pd.DataFrame(predicted_test)
res=res.rename(columns = {0:'Релевантность', 1:'Таксономия релевантные', 2:'Таксономия не релевантные', 3:'Длина отзыва', 4:'Ценности'})
res['RecordNo'] = df_test['RecordNo'] 
res = res[['RecordNo', 'Релевантность', 'Таксономия релевантные','Таксономия не релевантные', 'Длина отзыва', 'Ценности']]
res

RecordNo  Релевантность  Таксономия релевантные  \
0         3366              0                       0   
1         3952              0                       1   
2         6852              0                       0   
3         4586              0                       0   
4         4677              0                       1   
...        ...            ...                     ...   
2070      4661              0                       1   
2071      1547              0                       0   
2072      6071              1                       1   
2073      3805              0                       1   
2074       471              0                       0   

      Таксономия не релевантные  Длина отзыва  Ценности  
0                             0             1         1  
1                             0             0         0  
2                             0             0         1  
3                             0             0         1  
4                             0             0         0  
...                         ...           ...       ...  
2070                          1             0         1  
2071                          1             0         0  
2072                          0             0         1  
2073                          0             0         1  
2074                          0             0         1  

[2075 rows x 6 columns]

In [22]:
#выгрузим результаты в csv
res.to_csv('res.csv', index=False)